In [1]:
import os
import time
import pickle
import networkx as nx
import matplotlib.pyplot as plt

import numpy as np
from numpy import linalg as LA
from numpy import histogram2d

from scipy import signal
from scipy.fft import fft, fftfreq, fftshift
from scipy.signal import find_peaks, butter, filtfilt, welch
from scipy.ndimage import gaussian_filter
from scipy.io import wavfile

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix

import utils as ut
from utils import try_except_decorator
%load_ext autoreload
%autoreload 2

In [2]:
data_file = "../data/scooter_example_1.wav"
fs, data = wavfile.read(data_file)

# crop data
start_time = 60 # seconds
end_time = 160 # seconds
data = data[int(start_time*fs):int(end_time*fs)]

# data_file = "../data/12062025_example.wav"
# fs, data = wavfile.read(data_file)


# set time annotations
# 1st detection: 3-37 seconds
d1_start = 3
d1_end = 37
# 2nd detection: 91-143 seconds
d2_start = 91
d2_end = 143
# need to account for time cropping
time_annotations = np.zeros_like(data, dtype=int)
if d1_end > start_time and d1_start < end_time:
    s = max(d1_start, start_time) - start_time
    e = min(d1_end, end_time) - start_time
    time_annotations[int(s*fs):int(e*fs)] = 1
if d2_end > start_time and d2_start < end_time:
    s = max(d2_start, start_time) - start_time
    e = min(d2_end, end_time) - start_time
    time_annotations[int(s*fs):int(e*fs)] = 1
print(f"Sample rate: {fs} Hz")
print(f"Data shape: {data.shape}")
print(f"Positive Annotations: {np.sum(time_annotations)} samples, {np.sum(time_annotations)/fs} seconds")
print(f"Negative Annotations: {np.sum(time_annotations==0)} samples, {np.sum(time_annotations==0)/fs} seconds")

f, t, Sxx = ut.get_spectrogram(data, fs, crop_freq=2000)
ut.plot_spectrogram(f, t, Sxx)

/var/folders/3d/d9dsxkl92nz9mr2x53ct_fvh0000gn/T/ipykernel_47143/3615765980.py:2: WavFileWarning: Chunk (non-data) not understood, skipping it.
  fs, data = wavfile.read(data_file)


Sample rate: 128000 Hz
Data shape: (12800000,)
Positive Annotations: 6656000 samples, 52.0 seconds
Negative Annotations: 6144000 samples, 48.0 seconds


---

In [3]:
slices, slice_annotations = ut.slice_signal(data, time_annotations, fs, slice_duration=5.0)
print(f"Slices shape: {slices.shape}")
print(f"Slice Annotations shape: {slice_annotations.shape}")
print(f"Positive Slices: {np.sum(slice_annotations)}")
print(f"Negative Slices: {np.sum(slice_annotations==0)}")

Slices shape: (39, 640000)
Slice Annotations shape: (39,)
Positive Slices: 22
Negative Slices: 17


In [4]:
batch_size = 4
rand_ixs = [5, 35, 17, 25]  # np.random.choice(slices.shape[0], size=batch_size, replace=False)

print("Randomly selected slice indices:", rand_ixs)
print("Corresponding annotations:", slice_annotations[rand_ixs])
ut.plot_batch(slices, fs, slice_annotations, ixs=rand_ixs, crop_freq=2000, remove_dc=20, nperseg=32768)

Randomly selected slice indices: [5, 35, 17, 25]
Corresponding annotations: [0 0 1 1]


In [5]:
s = slices[17]
f, Pxx = ut.pwelch(s, fs, remove_dc=20, crop_freq=2000)

i = np.where(f >= 643.5)[0][0]
j = np.where(f >= 1281)[0][0]
print(f"i: {i}, f[i]: {f[i]}")
print(f"j: {j}, f[j]: {f[j]}")

i: 1287, f[i]: 643.5
j: 2562, f[j]: 1281.0


In [6]:
line = []
Pk = []
is_below = []
for k in range(i+1, j):
    x = (Pxx[i] + (Pxx[j] - Pxx[i]) * (k - i) / (j - i))
    line.append(x)
    Pk.append(Pxx[k])
    is_below.append(Pxx[k] < x)

fig = go.Figure()
fig.add_trace(go.Scatter(x=f, y=Pxx, mode='lines+markers', name='Pxx'))
fig.add_trace(go.Scatter(x=f[i+1:j], y=line, mode='lines', name='Line between i and j', line=dict(color='red', dash='dash')))
fig.add_trace(go.Scatter(x=f[i+1:j], y=Pk, mode='markers', name='Pxx between i and j', marker=dict(color='green', size=8)))
fig.update_layout(title='Pwelch with Line between Points i and j',
                  xaxis_title='Frequency (Hz)',
                  yaxis_title='Power/Frequency (V**2/Hz)')
fig.show()

In [8]:
vis = ut.calc_vis_graph(f, Pxx)

dots = np.where(vis == 1)
# plot the visibility graph points
fig = go.Figure()
fig.add_trace(go.Scatter(x=dots[0], y=dots[1], mode='markers', marker=dict(size=0.5, color='black')))
fig.update_layout(title='Visibility Graph Points from Pwelch',
                  xaxis_title='Frequency Index',
                  yaxis_title='Frequency Index',
                  width=600, height=600)

fig.show()

Processing node 1287 in range (0, 4001)
Processing node 1282 in range (0, 1287)
Processing node 1281 in range (0, 1282)
Processing node 1280 in range (0, 1281)
Processing node 69 in range (0, 1280)
Processing node 49 in range (0, 69)
Processing node 44 in range (0, 49)
Processing node 43 in range (0, 44)
Processing node 41 in range (0, 43)
Processing node 0 in range (0, 41)
Processing node 1 in range (1, 41)
Processing node 2 in range (2, 41)
Processing node 3 in range (3, 41)
Processing node 4 in range (4, 41)
Processing node 5 in range (5, 41)
Processing node 6 in range (6, 41)
Processing node 7 in range (7, 41)
Processing node 8 in range (8, 41)
Processing node 9 in range (9, 41)
Processing node 10 in range (10, 41)
Processing node 11 in range (11, 41)
Processing node 12 in range (12, 41)
Processing node 13 in range (13, 41)
Processing node 14 in range (14, 41)
Processing node 15 in range (15, 41)
Processing node 16 in range (16, 41)
Processing node 17 in range (17, 41)
Processing n

## Calculate Graph Degree Distribution

In [9]:
np.unique(np.diag(vis), return_counts=True)

(array([0.]), array([4001]))

In [ ]:
degrees = np.sum(vis, axis=1)

n_samples = degrees.shape[0]
nbins = int((n_samples/5)**.5)
histogram, _ = np.histogram(degrees, bins=nbins)
probs = histogram[1:]  # / len(degrees) + 1e-100

fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(1, len(probs)), y=probs, mode='lines+markers'))
fig.update_layout(title='Degree Distribution of Visibility Graph',
                  xaxis_title='Degree Bin',
                  yaxis_title='Probability',
                  width=700, height=500)
fig.show()

In [ ]:
degrees, counts = np.unique(np.sum(vis, axis=1), return_counts=True)
counts = counts / len(degrees) + 1e-100


fig = go.Figure()
fig.add_trace(go.Scatter(x=degrees, y=counts, mode='lines+markers'))
fig.update_layout(title='Degree Distribution of Visibility Graph',
                  xaxis_title='Degree',
                  yaxis_title='Probability',
                  width=700, height=500)
fig.show()